In [ ]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt

# from matplotlib.animation import FuncAnimation
# from mpl_toolkits.mplot3d import Axes3D
%matplotlib qt
from matplotlib.animation import FFMpegWriter

### 2D Wave Equation from Virieux 1984

Code is based on a method presented by Jean Virieux in his paper "SH-wave propagation in heterogeneous media: Velocity-stress finite-difference method" (1984). 



In [ ]:
# parameters 

# matrix size
m = 200
n = 400

# discretization values
dt = 0.1
dx = 1
dz = 1

Sigma = np.zeros([m,n])    # stress matrix that gets updated (vertical direction)
Sigmanew = np.zeros([m,n]) # stress matrix that gets updated within loop

Tau = np.zeros([m,n])      # stress matrix that gets updated (horizontal direction)
Taunew = np.zeros([m,n])   # stress matrix that gets updated within loop 

V = np.zeros([m,n])        # velocity matrix
Vnew = np.zeros([m,n])     # velocity matrix that gets updated 
L = np.zeros([m,n])        # 'lightness' (density) matrix 
M = np.zeros([m,n])        # shear modulus matrix


#setting all values to be equal within L and M 
L[:,:] = 1
M[:,:] = 2

# heterogeneous values and regions <--- change this for variations in simulations!
# M[80:100,160:240] = 3
# M[:,:80] = 4

# source excitation function
def sine(t): 
    f = 10 * np.sin(5*np.deg2rad(t))
    return f


In [ ]:
# setting up animation 
metadata = dict(title='displacement test', artist='Matplotlib',comment='no')
writer = FFMpegWriter(fps=60, metadata=metadata)
fig = plt.figure()

with writer.saving(fig, "velocity8.mp4", dpi=200):

    for t in range(0,2000,1):   
        
        for i in range(0,m,1):
            for j in range(0,n,1):
                
                if (i%2==0) & (j%2==0):
                    
                    
                    # stress computation
                    if (i < m-2) & (j < n-2):
                        Sigmanew[i+1,j] = Sigma[i+1,j] + ((dt/dz) * M[i+1,j] * (V[i+2,j] - V[i,j]))
                        Taunew[i,j+1] = Tau[i,j+1] + ((dt/dz) * M[i,j+1] * (V[i,j+2] - V[i,j]))
                    
                    
                    # boundary conditions for stress 
                    if i == m : 
                        Sigmanew[i-1,j] = Sigma[i-1,j] + ((dt/dz) * M[i-1,j] * (V[i-2,j] - V[i,j]))
                    
                    if j == n : 
                        Taunew[i,j-1] = Tau[i,j-1] + ((dt/dz) * M[i,j-1] * (V[i,j-2] - V[i,j]))
                        
        # updating stress matrices
        Sigma = Sigmanew
        Tau = Taunew
        
        for i in range(2,m-2,1):
            for j in range(2,n-2,1):
                
                # velocity computation
                if (i%2==0) & (j%2==0):
                    Vnew[i,j] = V[i,j] + ((dt/dx) * L[i,j] * (Sigmanew[i+1,j] - Sigmanew[i-1,j])) + ((dt/dz) * L[i,j] * (Taunew[i,j+1] - Taunew[i,j-1]))  
        #updating velocity matrix
        V = Vnew
        
        
        # source excitation location and duration
        if t<70:
            V[160,20] = sine(t)
        else:
            V[160,20] = 0 

        # plotting velocity and saving frame to animation
        plt.clf()
        plt.imshow(V[::2,::2],vmin=-5, vmax=5,cmap='magma')
        plt.title("2D Wave Equation Propagating Through Velocity Anomaly")
        plt.show()
        plt.draw()
        plt.pause(0.005)
        writer.grab_frame()
        
        # ticker 
        if t % 50 == 0:
            print('we are at',t)
        